# Download images

In [4]:
#imports
from fastbook import *
from fastai.vision.widgets import *
from tqdm.auto import tqdm

#download from duckduckgo
def search_images_ddg(key,max_n=200):
     """Search for 'key' with DuckDuckGo and return a unique urls of 'max_n' images
        (Adopted from https://github.com/deepanprabhu/duckduckgo-images-api)
     """
     url        = 'https://duckduckgo.com/'
     params     = {'q':key}
     res        = requests.post(url,data=params)
     searchObj  = re.search(r'vqd=([\d-]+)\&',res.text)
     if not searchObj: print('Token Parsing Failed !'); return
     requestUrl = url + 'i.js'
     headers    = {'User-Agent': 'Mozilla/5.0 (X11; Ubuntu; Linux x86_64; rv:71.0) Gecko/20100101 Firefox/71.0'}
     params     = (('l','us-en'),('o','json'),('q',key),('vqd',searchObj.group(1)),('f',',,,'),('p','1'),('v7exp','a'))
     urls       = []
     while True:
         try:
             res  = requests.get(requestUrl,headers=headers,params=params)
             data = json.loads(res.text)
             for obj in data['results']:
                 urls.append(obj['image'])
                 max_n = max_n - 1
                 if max_n < 1: return L(set(urls))     # dedupe
             if 'next' not in data: return L(set(urls))
             requestUrl = url + data['next']
         except:
             pass

## Download and Clean Data

In [5]:
path = Path('images')
cookie_types = ['chocolate chip','raisin']
MAX_N = 1000

if not path.exists():
    path.mkdir()
    for o in tqdm(cookie_types):
        dest = (path/o)
        dest.mkdir(exist_ok=True)
        results = search_images_ddg(f'{o} cookies', max_n=MAX_N)
        download_images(dest, urls=results)

In [6]:
fns = get_image_files(path)
fns

(#1678) [Path('images/raisin/00000645.jpg'),Path('images/raisin/00000362.jpg'),Path('images/raisin/00000482.jpg'),Path('images/raisin/00000366.jpg'),Path('images/raisin/00000270.jpg'),Path('images/raisin/00000435.jpg'),Path('images/raisin/00000227.jpg'),Path('images/raisin/00000739.jpg'),Path('images/raisin/00000127.jpg'),Path('images/raisin/00000134.jpg')...]

In [7]:
failed = verify_images(fns)
failed

/usr/local/lib/python3.7/dist-packages/PIL/TiffImagePlugin.py:788: UserWarning: Corrupt EXIF data.  Expecting to read 4 bytes but only got 0. 
  warnings.warn(str(msg))
/usr/local/lib/python3.7/dist-packages/PIL/TiffImagePlugin.py:788: UserWarning: Corrupt EXIF data.  Expecting to read 4 bytes but only got 0. 
  warnings.warn(str(msg))


(#19) [Path('images/raisin/00000414.jpg'),Path('images/raisin/00000002.jpg'),Path('images/raisin/00000689.jpg'),Path('images/raisin/00000123.jpg'),Path('images/raisin/00000803.jpg'),Path('images/raisin/00000651.jpg'),Path('images/raisin/00000293.jpg'),Path('images/raisin/00000243.jpg'),Path('images/raisin/00000377.jpg'),Path('images/raisin/00000465.jpg')...]

In [8]:
failed.map(Path.unlink);